In [ ]:
# First, upgrade numpy to version 2.x
!pip install --upgrade "numpy>=2.0,<2.3"

# Then install your required packages
!pip install pandas neo4j faiss-cpu sentence-transformers hdbscan spacy scispacy

# Install the scispacy model
!pip install https://s3-us-west-2.amazonaws.com/ai2-s2-scispacy/releases/v0.5.4/en_core_sci_lg-0.5.4.tar.gz

# Restart the runtime after installation
import os
os.kill(os.getpid(), 9)

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 62.0/62.0 kB 5.7 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 16.5/16.5 MB 124.6 MB/s eta 0:00:00
  Attempting uninstall: numpy
    Found existing installation: numpy 2.0.2
    Uninstalling numpy-2.0.2:
      Successfully uninstalled numpy-2.0.2
ERROR: pip's dependency resolver does not currently take into account all the packages that are installed. This behaviour is the source of the following dependency conflicts.
tensorflow 2.19.0 requires numpy<2.2.0,>=1.26.0, but you have numpy 2.2.6 which is incompatible.
numba 0.60.0 requires numpy<2.1,>=1.22, but you have numpy 2.2.6 which is incompatible.


     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 61.0/61.0 kB 6.7 MB/s eta 0:00:00
INFO: pip is looking at multiple versions of thinc to determine which version is compatible with other requirements. This could take a while.
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 325.8/325.8 kB 31.8 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 31.4/31.4 MB 93.7 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 62.6/62.6 kB 7.4 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 14.2/14.2 MB 17.7 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 18.0/18.0 MB 111.9 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 3.7/3.7 MB 95.6 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 71.1/71.1 kB 8.7 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 11.6/11.6 MB 78.4 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 293.6/293.6 kB 32.5 MB/s eta 0:00:00
  Attempting uninstall: numpy
    Found existing installation: num

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 531.2/531.2 MB 3.0 MB/s eta 0:00:00
  Preparing metadata (setup.py) ... done
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 6.5/6.5 MB 108.7 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 865.0/865.0 kB 67.9 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 10.2/10.2 MB 145.7 MB/s eta 0:00:00
  Created wheel for en_core_sci_lg: filename=en_core_sci_lg-0.5.4-py3-none-any.whl size=531476533 sha256=9b75d23698b7d58489ec6facefe4b13b237973841b358c215d609754a1774832
  Stored in directory: /root/.cache/pip/wheels/90/e0/2d/b68599c204c33cde8e8f5d3a0ff20bc3dff3a508bb9d350265
Successfully built en_core_sci_lg
  Attempting uninstall: blis
    Found existing installation: blis 1.2.1
    Uninstalling blis-1.2.1:
      Successfully uninstalled blis-1.2.1
  Attempting uninstall: thinc
    Found existing installation: thinc 8.3.4
    Uninstalling thinc-8.3.4:
      Successfully uninstalled thinc-8.3.4
  Attempting uninstall: spacy
    Fo

In [ ]:
# ONE-GO COLAB SCRIPT
# Paste and run in Colab (T4). Fill CONFIG fields below before running.

# ---------------------------
# 0) INSTALL & IMPORTS
# ---------------------------
#!pip install -q neo4j pandas tqdm scispacy spacy sentence-transformers hdbscan faiss-cpu
# scispacy models
#!pip install -q https://s3-us-west-2.amazonaws.com/ai2-s2-scispacy/releases/v0.5.1/en_core_sci_lg-0.5.1.tar.gz

import os, json, time, math, gc
from tqdm import tqdm
import pandas as pd
from neo4j import GraphDatabase
import numpy as np
import faiss
from sentence_transformers import SentenceTransformer
import hdbscan
import spacy
import scispacy
from collections import defaultdict
from hashlib import sha1

# load spacy scispacy model
nlp = spacy.load("en_core_sci_lg")

# ---------------------------
# CONFIG (FILL THESE)
# ---------------------------
NEO4J_URI = "HIDDEN"
NEO4J_USER = "HIDDEN"
NEO4J_PWD  = "HIDDEN"

OUT_DIR = "/content/graph_pipeline_out"
os.makedirs(OUT_DIR, exist_ok=True)

# Try multiple possible text property names
TEXT_PROPERTIES = ["name", "text", "description", "title", "label", "start_text", "end_text", "start_text_en", "end_text_en"]
ENTITY_LABEL = None

USE_UMLS = False
UMLS_LINKER_NAME = "umls"
CUI_PROPERTY = "cui"
CANONICAL_NAME_PROPERTY = "canonical_name"

EMBED_MODEL = "all-mpnet-base-v2"
EMBED_BATCH = 128
CLUSTER_MIN_SAMPLES = 5
CLUSTER_MIN_CLUSTER_SIZE = 2
EMBED_DIMS = 768

SIMILARITY_THRESHOLD = 0.82
TOP_K = 5

# ---------------------------
# HELPERS
# ---------------------------
def atomic_write_json(obj, path):
    tmp = path + ".tmp"
    with open(tmp, "w", encoding="utf-8") as f:
        json.dump(obj, f, ensure_ascii=False, indent=2)
    os.replace(tmp, path)

def atomic_write_df(df, path):
    tmp = path + ".tmp"
    df.to_csv(tmp, index=False)
    os.replace(tmp, path)

def uid(s):
    return sha1(str(s).encode("utf-8")).hexdigest()

# ---------------------------
# CONNECT TO NEO4J AURA
# ---------------------------
print("Connecting to Neo4j...")
driver = GraphDatabase.driver(NEO4J_URI, auth=(NEO4J_USER, NEO4J_PWD), max_connection_lifetime=3600)

# Test connection
try:
    with driver.session() as s:
        result = s.run("RETURN 1 as test")
        result.single()
        print("✓ Connected to Neo4j successfully")
except Exception as e:
    print(f"✗ Failed to connect to Neo4j: {e}")
    raise

# ---------------------------
# 1) DISCOVER NODES & AVAILABLE PROPERTIES
# ---------------------------
print("\n=== Step 1: Discovering nodes and properties ===")
discovery_csv = os.path.join(OUT_DIR, "discovered_nodes.csv")

# First, check what labels and properties exist in the database
print("Inspecting database schema...")
with driver.session() as s:
    # Get all node labels
    labels_result = s.run("CALL db.labels()")
    labels = [r[0] for r in labels_result]
    print(f"Available labels: {labels}")

    # Get sample nodes to inspect properties
    sample_result = s.run("MATCH (n) RETURN n LIMIT 5")
    sample_nodes = list(sample_result)

    if not sample_nodes:
        print("✗ ERROR: Database appears to be empty!")
        print("Please ensure your CSV data has been imported into Neo4j.")
        driver.close()
        exit(1)

    # Extract all property keys from sample
    all_props = set()
    for record in sample_nodes:
        node = record["n"]
        all_props.update(node.keys())

    print(f"Available properties in sample: {sorted(all_props)}")

# Build query to find nodes with text properties
available_text_props = [p for p in TEXT_PROPERTIES if p in all_props]

if not available_text_props:
    # Fallback: try to find any string property
    print("⚠ Warning: None of the expected text properties found. Scanning for any text properties...")
    with driver.session() as s:
        result = s.run("""
        MATCH (n)
        WITH n LIMIT 10
        UNWIND keys(n) AS key
        WITH DISTINCT key, n[key] AS value
        WHERE value IS NOT NULL AND toString(value) <> ''
        RETURN DISTINCT key
        """)
        available_text_props = [r["key"] for r in result]
    print(f"Found possible text properties: {available_text_props}")

if not available_text_props:
    print("✗ ERROR: Could not find any text properties in the database!")
    print("Please check your data import. Nodes should have at least one text property.")
    driver.close()
    exit(1)

# Build conditions for query
prop_checks_list = []
select_props = []
for p in available_text_props:
    prop_checks_list.append(f"(n.`{p}` IS NOT NULL AND toString(n.`{p}`) <> '')")
    select_props.append(f"n.`{p}` AS `{p}`")

prop_checks = " OR ".join(prop_checks_list)

q = f"""
MATCH (n)
WHERE {prop_checks}
RETURN elementId(n) AS nid,
       {', '.join(select_props)}
LIMIT 100000
"""

print(f"Executing discovery query...")
rows = []
with driver.session() as s:
    res = s.run(q)
    for r in res:
        row = {"nid": r["nid"]}
        for p in available_text_props:
            val = r.get(p, None)
            row[p] = str(val) if val is not None else None
        rows.append(row)

if not rows:
    print("✗ ERROR: No nodes with text properties found!")
    print("Please verify your data has been imported correctly.")
    driver.close()
    exit(1)

nodes_df = pd.DataFrame(rows)
atomic_write_df(nodes_df, discovery_csv)
print(f"✓ Discovered {len(nodes_df)} nodes. Saved to {discovery_csv}")

# Pick canonical text for each node
def choose_text(row):
    for p in available_text_props:
        v = row.get(p, None)
        if isinstance(v, str) and v.strip():
            return v.strip()
    return ""

nodes_df["text"] = nodes_df.apply(lambda r: choose_text(r), axis=1)
nodes_df["text"] = nodes_df["text"].fillna("").astype(str)
nodes_df = nodes_df[nodes_df["text"].str.strip() != ""]

if len(nodes_df) == 0:
    print("✗ ERROR: No nodes with valid text content found after filtering!")
    driver.close()
    exit(1)

atomic_write_df(nodes_df, discovery_csv)
print(f"✓ Nodes with text to process: {len(nodes_df)}")

# ---------------------------
# 2) Named Entity Extraction (SciSpacy)
# ---------------------------
print("\n=== Step 2: Named Entity Recognition ===")
ner_progress = os.path.join(OUT_DIR, "ner_progress.csv")
if os.path.exists(ner_progress):
    ner_df = pd.read_csv(ner_progress)
    print(f"✓ Loaded existing NER progress: {len(ner_df)} nodes")
else:
    print("Running NER extraction on node texts...")
    rows = []
    for idx, row in tqdm(nodes_df.iterrows(), total=len(nodes_df), desc="NER Processing"):
        nid = row["nid"]
        text = row["text"]

        doc = nlp(text[:2000])
        ents = []
        for e in doc.ents:
            ents.append({"text": e.text, "label": e.label_})

        if not ents:
            nchs = [nc.text for nc in doc.noun_chunks][:3]
            if nchs:
                ents = [{"text": t, "label": "NOUN_CHUNK"} for t in nchs]
            else:
                ents = [{"text": text[:120], "label": "SENT"}]

        rows.append({
            "nid": nid,
            "text": text,
            "entities": json.dumps(ents, ensure_ascii=False)
        })

    ner_df = pd.DataFrame(rows)
    atomic_write_df(ner_df, ner_progress)
    print(f"✓ NER extraction completed and saved")

# ---------------------------
# 3) Canonicalization via Clustering
# ---------------------------
print("\n=== Step 3: Canonicalization ===")
canon_progress = os.path.join(OUT_DIR, "canonicalization.csv")
if os.path.exists(canon_progress):
    canon_df = pd.read_csv(canon_progress)
    print(f"✓ Loaded existing canonicalization: {len(canon_df)} nodes")
else:
    print("Building canonical names/ids using embeddings & clustering...")
    texts = ner_df["text"].tolist()
    nids = ner_df["nid"].tolist()

    emb_model = SentenceTransformer(EMBED_MODEL)
    embeddings = []
    for i in tqdm(range(0, len(texts), EMBED_BATCH), desc="Computing embeddings"):
        batch_texts = texts[i:i+EMBED_BATCH]
        embs = emb_model.encode(batch_texts, convert_to_numpy=True, show_progress_bar=False)
        embeddings.append(embs)
    embeddings = np.vstack(embeddings).astype('float32')
    print(f"✓ Embeddings shape: {embeddings.shape}")

    print("Running HDBSCAN clustering...")
    clusterer = hdbscan.HDBSCAN(
        min_cluster_size=CLUSTER_MIN_CLUSTER_SIZE,
        min_samples=CLUSTER_MIN_SAMPLES,
        metric='euclidean',
        cluster_selection_method='eom'
    )
    cluster_labels = clusterer.fit_predict(embeddings)
    n_clusters = len(set(cluster_labels)) - (1 if -1 in cluster_labels else 0)
    print(f"✓ Found {n_clusters} clusters")

    canon_rows = []
    label_to_ids = defaultdict(list)
    for i, lbl in enumerate(cluster_labels):
        label_to_ids[lbl].append(i)

    for lbl, idxs in tqdm(label_to_ids.items(), desc="Creating canonical entries"):
        if lbl == -1:
            for idx in idxs:
                nid = nids[idx]
                name = texts[idx][:200]
                cid = uid(name + str(lbl) + str(idx))
                canon_rows.append({
                    "nid": nid,
                    "canonical_id": cid,
                    "canonical_name": name,
                    "cluster": int(lbl)
                })
        else:
            pts = embeddings[idxs]
            centroid = pts.mean(axis=0)
            dists = np.linalg.norm(pts - centroid, axis=1)
            best_local = idxs[int(np.argmin(dists))]
            canonical_name = texts[best_local][:200]
            canonical_id = uid(canonical_name + str(lbl))

            for idx in idxs:
                nid = nids[idx]
                canon_rows.append({
                    "nid": nid,
                    "canonical_id": canonical_id,
                    "canonical_name": canonical_name,
                    "cluster": int(lbl)
                })

    canon_df = pd.DataFrame(canon_rows)
    atomic_write_df(canon_df, canon_progress)
    print(f"✓ Canonicalization saved: {len(canon_df)} entries")

# ---------------------------
# 4) WRITE BACK canonical properties
# ---------------------------
print("\n=== Step 4: Writing canonical properties to Neo4j ===")
write_progress = os.path.join(OUT_DIR, "write_back_progress.csv")
if os.path.exists(write_progress):
    wrote_df = pd.read_csv(write_progress)
    wrote_nids = set(wrote_df["nid"].tolist())
    print(f"✓ Loaded write progress: {len(wrote_df)} nodes already written")
else:
    wrote_df = pd.DataFrame(columns=["nid","canonical_id","canonical_name","written"])
    wrote_nids = set()

to_write = canon_df[~canon_df["nid"].isin(wrote_nids)]
print(f"Nodes to write: {len(to_write)}")

if len(to_write) > 0:
    BATCH = 100
    for i in tqdm(range(0, len(to_write), BATCH), desc="Writing to Neo4j"):
        chunk = to_write.iloc[i:i+BATCH]
        with driver.session() as s:
            for _, r in chunk.iterrows():
                nid = r["nid"]
                cid = r["canonical_id"]
                cname = r["canonical_name"]

                try:
                    s.run("""
                    MATCH (n) WHERE elementId(n) = $nid
                    SET n.canonical_id = $cid, n.canonical_name = $cname
                    """, nid=nid, cid=cid, cname=cname)
                except Exception as e:
                    print(f"Error writing node {nid}: {e}")

        recs = [{
            "nid": r["nid"],
            "canonical_id": r["canonical_id"],
            "canonical_name": r["canonical_name"],
            "written": True
        } for _, r in chunk.iterrows()]
        wrote_df = pd.concat([wrote_df, pd.DataFrame(recs)], ignore_index=True)
        atomic_write_df(wrote_df, write_progress)

    print("✓ Canonical properties written to Neo4j")

# ---------------------------
# 5) CREATE CANONICAL NODES & MERGE
# ---------------------------
print("\n=== Step 5: Creating canonical nodes ===")
merge_progress = os.path.join(OUT_DIR, "merge_progress.csv")
if os.path.exists(merge_progress):
    merged_df = pd.read_csv(merge_progress)
    merged_cids = set(merged_df["canonical_id"].tolist())
    print(f"✓ Loaded merge progress: {len(merged_df)} canonical nodes")
else:
    merged_df = pd.DataFrame(columns=["canonical_id","canonical_node_id","done"])
    merged_cids = set()

groups = canon_df.groupby("canonical_id").agg({
    "nid": list,
    "canonical_name": "first"
}).reset_index()

to_merge = groups[~groups["canonical_id"].isin(merged_cids)]
print(f"Canonical groups to create: {len(to_merge)}")

if len(to_merge) > 0:
    with driver.session() as s:
        for idx, row in tqdm(to_merge.iterrows(), total=len(to_merge), desc="Creating canonical nodes"):
            cid = row["canonical_id"]
            cname = row["canonical_name"]
            nlist = row["nid"]

            try:
                result = s.run("""
                MERGE (c:EntityCanonical {canonical_id: $cid})
                ON CREATE SET c.name = $cname
                RETURN elementId(c) as cid
                """, cid=cid, cname=cname)

                canonical_node_id = result.single()["cid"]

                # Link original nodes to canonical node
                for nid in nlist:
                    s.run("""
                    MATCH (n) WHERE elementId(n) = $nid
                    MATCH (c:EntityCanonical {canonical_id: $cid})
                    MERGE (n)-[:CANONICAL_FORM]->(c)
                    """, nid=nid, cid=cid)

                merged_df = pd.concat([merged_df, pd.DataFrame([{
                    "canonical_id": cid,
                    "canonical_node_id": canonical_node_id,
                    "done": True
                }])], ignore_index=True)

                if idx % 50 == 0:
                    atomic_write_df(merged_df, merge_progress)

            except Exception as e:
                print(f"Error creating canonical node {cid}: {e}")

        atomic_write_df(merged_df, merge_progress)

    print("✓ Canonical nodes created and linked")

# ---------------------------
# 6) COMPUTE & STORE EMBEDDINGS
# ---------------------------
print("\n=== Step 6: Computing embeddings for canonical nodes ===")
emb_progress = os.path.join(OUT_DIR, "embeddings_written.csv")
if os.path.exists(emb_progress):
    emb_written = pd.read_csv(emb_progress)
    written_ids = set(emb_written["canonical_node_id"].tolist())
else:
    emb_written = pd.DataFrame(columns=["canonical_node_id","written"])
    written_ids = set()

with driver.session() as s:
    res = s.run("MATCH (c:EntityCanonical) RETURN elementId(c) as cid, c.name as name")
    c_rows = [{"cid": r["cid"], "name": r["name"] or ""} for r in res]

c_df = pd.DataFrame(c_rows)
to_embed = c_df[~c_df["cid"].isin(written_ids)]
print(f"Canonical nodes to embed: {len(to_embed)}")

if len(to_embed) > 0:
    embed_model = SentenceTransformer(EMBED_MODEL)
    B = 64

    for i in tqdm(range(0, len(to_embed), B), desc="Computing & storing embeddings"):
        batch = to_embed.iloc[i:i+B]
        names = batch["name"].fillna("").tolist()
        embs = embed_model.encode(names, convert_to_numpy=True, show_progress_bar=False)

        with driver.session() as s:
            for cid, vec in zip(batch["cid"], embs):
                try:
                    s.run("""
                    MATCH (c) WHERE elementId(c) = $cid
                    SET c.text_emb = $vec
                    """, cid=cid, vec=vec.tolist())
                except Exception as e:
                    print(f"Error writing embedding for {cid}: {e}")

        recs = [{"canonical_node_id": cid, "written": True} for cid in batch["cid"]]
        emb_written = pd.concat([emb_written, pd.DataFrame(recs)], ignore_index=True)
        atomic_write_df(emb_written, emb_progress)

    print("✓ Embeddings computed and stored")

# ---------------------------
# 7) CREATE SIMILARITY LINKS
# ---------------------------
print("\n=== Step 7: Creating semantic similarity links ===")
sim_progress = os.path.join(OUT_DIR, "sim_links.csv")

with driver.session() as s:
    res = s.run("""
    MATCH (c:EntityCanonical)
    WHERE c.text_emb IS NOT NULL
    RETURN elementId(c) as cid, c.text_emb as vec
    """)
    data = [(r["cid"], np.array(r["vec"], dtype='float32')) for r in res]

if not data:
    print("⚠ No canonical nodes with embeddings found - skipping similarity links")
else:
    ids, vecs = zip(*data)
    ids = np.array(ids)
    vecs = np.vstack(vecs).astype('float32')

    faiss.normalize_L2(vecs)
    index = faiss.IndexFlatIP(vecs.shape[1])
    index.add(vecs)

    print(f"Computing top-{TOP_K} similarities for {len(vecs)} nodes...")
    D, I = index.search(vecs, TOP_K+1)

    pairs = []
    for i_row, src_id in enumerate(ids):
        for rank in range(1, min(TOP_K+1, I.shape[1])):
            dst_idx = I[i_row, rank]
            score = float(D[i_row, rank])
            if score >= SIMILARITY_THRESHOLD:
                dst_id = ids[dst_idx]
                pairs.append({"src": src_id, "dst": dst_id, "score": score})

    print(f"Creating {len(pairs)} SIMILAR_TO relationships...")
    with driver.session() as s:
        for i in tqdm(range(0, len(pairs), 100), desc="Writing similarity links"):
            batch = pairs[i:i+100]
            for p in batch:
                try:
                    s.run("""
                    MATCH (a) WHERE elementId(a) = $a
                    MATCH (b) WHERE elementId(b) = $b
                    MERGE (a)-[r:SIMILAR_TO]->(b)
                    SET r.score = $score
                    """, a=p["src"], b=p["dst"], score=p["score"])
                except Exception as e:
                    print(f"Error creating similarity link: {e}")

    sim_df = pd.DataFrame(pairs)
    atomic_write_df(sim_df, sim_progress)
    print(f"✓ Created {len(pairs)} similarity relationships")

# ---------------------------
# 8) FINAL REPORTS
# ---------------------------
print("\n=== Step 8: Generating final reports ===")

with driver.session() as s:
    res = s.run("""
    MATCH (c:EntityCanonical)
    RETURN elementId(c) as cid, c.name as name, c.canonical_id as canonical_id
    LIMIT 100000
    """)
    rows = [{
        "cid": r["cid"],
        "name": r["name"],
        "canonical_id": r.get("canonical_id", None)
    } for r in res]

final_df = pd.DataFrame(rows)
final_csv = os.path.join(OUT_DIR, "canonical_nodes_summary.csv")
atomic_write_df(final_df, final_csv)

print(f"\n✓ Pipeline completed successfully!")
print(f"✓ Total canonical nodes created: {len(final_df)}")
print(f"✓ All outputs saved to: {OUT_DIR}")
print(f"\nGenerated files:")
for f in sorted(os.listdir(OUT_DIR)):
    fpath = os.path.join(OUT_DIR, f)
    size = os.path.getsize(fpath) / 1024
    print(f"  - {f} ({size:.1f} KB)")

driver.close()
print("\n✓ Connection closed. Pipeline complete!")

/usr/local/lib/python3.12/dist-packages/hdbscan/robust_single_linkage_.py:175: SyntaxWarning: invalid escape sequence '\{'
  $max \{ core_k(a), core_k(b), 1/\alpha d(a,b) \}$.
/usr/local/lib/python3.12/dist-packages/spacy/language.py:2195: FutureWarning: Possible set union at position 6328
  deserializers["tokenizer"] = lambda p: self.tokenizer.from_disk(  # type: ignore[union-attr]


Connecting to Neo4j...
✓ Connected to Neo4j successfully

=== Step 1: Discovering nodes and properties ===
Inspecting database schema...
Available labels: ['[Info Tree Node]', '[Info Tree Root]', '[Disease]', '[Embedding Root]', '[Embedding Node, pseudo medical history Embedding Node]', '[Embedding Node, diagnosis info Embedding Node]', 'Disease', 'Info Tree Node']
Available properties in sample: ['canonical_id', 'canonical_name', 'embedding', 'original_id', 'text']
Executing discovery query...
✓ Discovered 44637 nodes. Saved to /content/graph_pipeline_out/discovered_nodes.csv
✓ Nodes with text to process: 44637

=== Step 2: Named Entity Recognition ===
Running NER extraction on node texts...


NER Processing: 100%|██████████| 44637/44637 [08:35<00:00, 86.62it/s] 


✓ NER extraction completed and saved

=== Step 3: Canonicalization ===
Building canonical names/ids using embeddings & clustering...


/usr/local/lib/python3.12/dist-packages/huggingface_hub/utils/_auth.py:94: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(


...

✓ Canonical nodes created and linked

=== Step 6: Computing embeddings for canonical nodes ===
Canonical nodes to embed: 32694


Computing & storing embeddings: 100%|██████████| 511/511 [05:21<00:00,  1.59it/s]


✓ Embeddings computed and stored

=== Step 7: Creating semantic similarity links ===
Computing top-5 similarities for 32694 nodes...
Creating 21040 SIMILAR_TO relationships...


Writing similarity links: 100%|██████████| 211/211 [01:31<00:00,  2.31it/s]


✓ Created 21040 similarity relationships

=== Step 8: Generating final reports ===

✓ Pipeline completed successfully!
✓ Total canonical nodes created: 32694
✓ All outputs saved to: /content/graph_pipeline_out

Generated files:
  - canonical_nodes_summary.csv (7390.8 KB)
  - canonicalization.csv (9152.4 KB)
  - discovered_nodes.csv (14073.1 KB)
  - embeddings_written.csv (1596.4 KB)
  - merge_progress.csv (2905.5 KB)
  - ner_progress.csv (44029.6 KB)
  - sim_links.csv (2215.9 KB)
  - write_back_progress.csv (9222.1 KB)

✓ Connection closed. Pipeline complete!


In [ ]:
# --- ✅ One-Go Resumable Neo4j Medical Graph Finalization Script ---
# (Run in Colab; tested on CPU/T4)

!pip -q install neo4j pandas tqdm sentence-transformers hdbscan umap-learn google-auth google-auth-oauthlib google-auth-httplib2 gdown

import os, time, shutil, pandas as pd
from tqdm import tqdm
from neo4j import GraphDatabase
from sentence_transformers import SentenceTransformer
import hdbscan, numpy as np

# === 1️⃣ CONFIG ===
URI="HIDDEN"
AUTH=("neo4j","HIDDEN")
OUT_DIR="/content/graph_pipeline_out"
DRIVE_DIR="HIDDEN"
os.makedirs(OUT_DIR,exist_ok=True)

TEXT_PROPERTIES=["text"]
CANONICAL_FILE=f"{OUT_DIR}/canonicalization.csv"

# === 2️⃣ Connect ===
print("Connecting to Neo4j Aura...")
driver=GraphDatabase.driver(URI,auth=AUTH)
print("✓ Connected")

# === 3️⃣ Discovery (resumable) ===
disc_path=f"{OUT_DIR}/discovered_nodes.csv"
if os.path.exists(disc_path):
    print("⏩ Skipping discovery (already done)")
    nodes_df=pd.read_csv(disc_path)
else:
    print("Discovering nodes...")
    q="MATCH (n) WHERE n.text IS NOT NULL AND n.text<>'' RETURN id(n) AS nid,n.text AS text"
    rows=[]
    with driver.session() as s:
        for r in s.run(q): rows.append({"nid":r["nid"],"text":r["text"]})
    nodes_df=pd.DataFrame(rows)
    nodes_df.to_csv(disc_path,index=False)
    print(f"✓ Discovered {len(nodes_df)} nodes")

# === 4️⃣ NER Placeholder (resumable) ===
ner_path=f"{OUT_DIR}/ner_progress.csv"
if os.path.exists(ner_path):
    print("⏩ Skipping NER (already done)")
else:
    print("Running NER (mock for now)...")
    nodes_df["entities"]=nodes_df["text"].apply(lambda x:[x])
    nodes_df.to_csv(ner_path,index=False)
    print("✓ NER complete")

# === 5️⃣ Canonicalization (resumable) ===
if os.path.exists(CANONICAL_FILE):
    print("⏩ Skipping canonicalization (already done)")
    canonical_df=pd.read_csv(CANONICAL_FILE)
else:
    print("Building embeddings and clusters...")
    mdl=SentenceTransformer("sentence-transformers/all-MiniLM-L6-v2")
    emb=mdl.encode(nodes_df["text"].tolist(),batch_size=32,show_progress_bar=True)
    clusterer=hdbscan.HDBSCAN(min_cluster_size=5,metric='euclidean',cluster_selection_method='eom')
    labels=clusterer.fit_predict(emb)
    nodes_df["cluster"]=labels
    canonical_df=nodes_df.groupby("cluster")["nid"].apply(list).reset_index().rename(columns={"nid":"members"})
    canonical_df.to_csv(CANONICAL_FILE,index=False)
    print("✓ Canonicalization saved")

# === 6️⃣ Write canonical nodes back ===
write_back=f"{OUT_DIR}/write_back_progress.csv"
if os.path.exists(write_back):
    print("⏩ Skipping write-back (already done)")
else:
    print("Writing canonical nodes to Neo4j...")
    with driver.session() as s:
        for _,r in tqdm(canonical_df.iterrows(),total=len(canonical_df)):
            if r["cluster"]==-1: continue
            name=f"Canonical_{r['cluster']}"
            s.run("MERGE (c:EntityCanonical {canonical_name:$name}) "
                  "SET c.canonical_id=$cid",
                  name=name,cid=str(r["cluster"]))
            for nid in r["members"]:
                s.run("MATCH (n) WHERE id(n)=$id "
                      "MATCH (c:EntityCanonical {canonical_id:$cid}) "
                      "MERGE (n)-[:CANONICAL_FORM]->(c)",
                      id=int(nid),cid=str(r["cluster"]))
    pd.DataFrame({"done":[True]}).to_csv(write_back,index=False)
    print("✓ Write-back complete")

# === 7️⃣ Generate Reports ===
print("Generating reports...")
summary_path=f"{OUT_DIR}/canonical_nodes_summary.csv"
canonical_df["member_count"]=canonical_df["members"].apply(len)
canonical_df.to_csv(summary_path,index=False)
print("✓ Reports generated at",OUT_DIR)

# === 8️⃣ Clean duplicates (light) ===
print("Running duplicate cleanup...")
with driver.session() as s:
    s.run("""
        MATCH (c:EntityCanonical)
        WITH c.canonical_id AS id, collect(c) AS cs
        WHERE size(cs)>1
        CALL {
            WITH cs
            UNWIND tail(cs) AS dupe
            DETACH DELETE dupe
        } IN TRANSACTIONS OF 100 ROWS
    """)
print("✓ Duplicate cleanup done")

# === 9️⃣ Backup to Google Drive ===
#from google.colab import drive
#drive.mount('/content/drive',force_remount=True)
os.makedirs(DRIVE_DIR,exist_ok=True)
for f in os.listdir(OUT_DIR):
    shutil.copy(os.path.join(OUT_DIR,f),os.path.join(DRIVE_DIR,f))
print(f"✓ All reports backed up to {DRIVE_DIR}")

# === 10️⃣ Final status ===
print("\n=== ✅ Pipeline completed ===")
print(f"Total canonical groups: {canonical_df.shape[0]}")
print(f"Outputs saved in {OUT_DIR} and backed up to Drive")
driver.close()

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 325.8/325.8 kB 12.6 MB/s eta 0:00:00


/usr/local/lib/python3.12/dist-packages/hdbscan/robust_single_linkage_.py:175: SyntaxWarning: invalid escape sequence '\{'
  $max \{ core_k(a), core_k(b), 1/\alpha d(a,b) \}$.


Connecting to Neo4j Aura...
✓ Connected
Discovering nodes...


✓ Discovered 44637 nodes
Running NER (mock for now)...
✓ NER complete
Building embeddings and clusters...


/usr/local/lib/python3.12/dist-packages/huggingface_hub/utils/_auth.py:94: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(


...

/usr/local/lib/python3.12/dist-packages/sklearn/utils/deprecation.py:151: FutureWarning: 'force_all_finite' was renamed to 'ensure_all_finite' in 1.6 and will be removed in 1.8.
  warnings.warn(
/usr/local/lib/python3.12/dist-packages/sklearn/utils/deprecation.py:151: FutureWarning: 'force_all_finite' was renamed to 'ensure_all_finite' in 1.6 and will be removed in 1.8.
  warnings.warn(


✓ Canonicalization saved
Writing canonical nodes to Neo4j...


Streaming output truncated to the last 5000 lines.
100%|██████████| 1064/1064 [57:04<00:00,  3.22s/it]


✓ Write-back complete
Generating reports...
✓ Reports generated at /content/graph_pipeline_out
Running duplicate cleanup...


✓ Duplicate cleanup done
✓ All reports backed up to /content/drive/MyDrive/SceneSolverG388/EnrichmentReport

=== ✅ Pipeline completed ===
Total canonical groups: 1064
Outputs saved in /content/graph_pipeline_out and backed up to Drive


In [ ]:
# ===========================================================
# FIXED ✅ Neo4j Semantic Graph Report & Backup Script
# ===========================================================
!pip -q install neo4j pandas tqdm

from neo4j import GraphDatabase
import pandas as pd, os, shutil
from tqdm import tqdm

# --- CONFIG ---
URI = "HIDDEN"
USER = "neo4j"
PASSWORD = "HIDDEN"
OUT_DIR = "/content/graph_pipeline_out"
DRIVE_DIR = "HIDDEN"

os.makedirs(OUT_DIR, exist_ok=True)

# --- CONNECT ---
driver = GraphDatabase.driver(URI, auth=(USER, PASSWORD))
print("✓ Connected to Neo4j")

# --- Helper (resumable save) ---
def save_df(df, name):
    p = f"{OUT_DIR}/{name}.csv"
    df.to_csv(p, index=False)
    print(f"✓ {name}.csv → {len(df)} rows")

# ===========================================================
# 1️⃣ Canonicalization Mapping
# ===========================================================
if not os.path.exists(f"{OUT_DIR}/canonicalization.csv"):
    print("Generating canonicalization.csv ...")
    q1 = """
    MATCH (n)-[:CANONICAL_FORM]->(c:EntityCanonical)
    RETURN n.original_id AS original_id,
           n.text AS text,
           c.canonical_id AS canonical_id,
           c.canonical_name AS canonical_name
    """
    with driver.session() as s:
        df1 = pd.DataFrame(s.run(q1).data())
    save_df(df1, "canonicalization")

# ===========================================================
# 2️⃣ Canonical Node Summary
# ===========================================================
if not os.path.exists(f"{OUT_DIR}/canonical_nodes_summary.csv"):
    print("Generating canonical_nodes_summary.csv ...")
    q2 = """
    MATCH (c:EntityCanonical)
    RETURN c.canonical_id AS canonical_id,
           c.canonical_name AS canonical_name,
           COUNT { (c)<-[:CANONICAL_FORM]-() } AS members
    """
    with driver.session() as s:
        df2 = pd.DataFrame(s.run(q2).data())
    save_df(df2, "canonical_nodes_summary")

# ===========================================================
# 3️⃣ Similarity Links
# ===========================================================
if not os.path.exists(f"{OUT_DIR}/sim_links.csv"):
    print("Generating sim_links.csv ...")
    q3 = """
    MATCH (a:EntityCanonical)-[r:SIMILAR_TO]->(b:EntityCanonical)
    RETURN a.canonical_id AS src,
           b.canonical_id AS tgt,
           r.score AS score
    """
    with driver.session() as s:
        df3 = pd.DataFrame(s.run(q3).data())
    save_df(df3, "sim_links")

# ===========================================================
# 4️⃣ Discovered Nodes
# ===========================================================
if not os.path.exists(f"{OUT_DIR}/discovered_nodes.csv"):
    print("Generating discovered_nodes.csv ...")
    q4 = """
    MATCH (n)
    WHERE n.text IS NOT NULL
    RETURN n.original_id AS id,
           labels(n) AS labels,
           n.text AS text
    """
    with driver.session() as s:
        df4 = pd.DataFrame(s.run(q4).data())
    save_df(df4, "discovered_nodes")

driver.close()
print("✓ All reports generated successfully")

# ===========================================================
# 5️⃣ Backup to Google Drive
# ===========================================================
print("Mounting Google Drive...")
from google.colab import drive
drive.mount('/content/drive', force_remount=True)

os.makedirs(DRIVE_DIR, exist_ok=True)
for f in tqdm(os.listdir(OUT_DIR), desc="Backing up to Drive"):
    shutil.copy2(os.path.join(OUT_DIR, f), os.path.join(DRIVE_DIR, f))
print(f"✓ All reports backed up to: {DRIVE_DIR}")

✓ Connected to Neo4j
Generating discovered_nodes.csv ...
✓ discovered_nodes.csv → 46129 rows
✓ All reports generated successfully
Mounting Google Drive...
Mounted at /content/drive


Backing up to Drive: 100%|██████████| 4/4 [00:00<00:00,  5.24it/s]

✓ All reports backed up to: /content/drive/MyDrive/SceneSolverG388/EnrichmentReport


In [ ]:
# Install the library for this session
%pip install -q sentence-transformers

from sentence_transformers import SentenceTransformer

model = SentenceTransformer('all-MiniLM-L6-v2')
patient_query = "I have a sharp pain in my chest and difficulty breathing."
query_embedding = model.encode(patient_query).tolist()

print("Copy the list of numbers below:")
print(query_embedding)

Copy the list of numbers below:
[0.08395948261022568, -0.016385160386562347, 0.005687599070370197, 0.06713096797466278, 0.05482710897922516, -0.06561823934316635, -0.07448691874742508, 0.056142713874578476, -0.0020117375534027815, -0.07352855801582336, -0.04163992032408714, -0.015145426616072655, 0.009485315531492233, 0.10022114962339401, 0.06308425217866898, -0.039074722677469254, 0.023103253915905952, 0.005952358245849609, 0.026636917144060135, 0.0647168830037117, -0.006900017615407705, 0.1431102156639099, -0.061749134212732315, -0.020277682691812515, -0.0348048135638237, 0.00860269833356142, -0.01991606131196022, -0.04130639508366585, 0.03331762179732323, -0.00014228251529857516, 0.09734705090522766, -0.0894271582365036, 0.02172267436981201, 0.042957939207553864, 0.05074452608823776, 0.07078764587640762, -0.041205160319805145, 0.06990419328212738, 0.005169946234673262, -0.019752060994505882, 0.020558947697281837, 0.07308574765920639, -0.03349360451102257, -0.029331086203455925, 0.03